In [79]:
import pandas as pd
import plotly.express as px
from datetime import datetime
import MetaTrader5 as mt5
from account_credentials import LOGIN, PASSWORD, SERVER

In [80]:
mt5.initialize()
mt5.login(LOGIN, PASSWORD, SERVER)

True

In [81]:
symbol = 'DE40'
timeframe = mt5.TIMEFRAME_M5
start_date = datetime(2022, 1, 1)
end_date = datetime(2022, 7, 1)
trade_volume = 0.5
commission = 1

In [82]:
bars = pd.DataFrame(mt5.copy_rates_range(symbol, timeframe, start_date, end_date))
bars['time'] = pd.to_datetime(bars['time'], unit='s')
bars['trade_volume'] = trade_volume
bars

time     open     high      low    close  tick_volume  \
0     2022-01-03 02:15:00  15886.7  15889.2  15881.2  15884.0           32   
1     2022-01-03 02:20:00  15884.0  15900.0  15884.0  15900.0           42   
2     2022-01-03 02:25:00  15903.0  15938.0  15902.5  15938.0           74   
3     2022-01-03 02:30:00  15936.0  15936.0  15918.0  15918.0           36   
4     2022-01-03 02:35:00  15918.0  15925.5  15911.5  15911.5           29   
...                   ...      ...      ...      ...      ...          ...   
34192 2022-06-30 21:40:00  12817.2  12817.2  12788.2  12789.2          282   
34193 2022-06-30 21:45:00  12788.2  12801.2  12786.7  12795.7          263   
34194 2022-06-30 21:50:00  12795.2  12797.2  12778.7  12785.7          247   
34195 2022-06-30 21:55:00  12785.2  12789.2  12780.2  12786.2          232   
34196 2022-06-30 22:00:00  12785.7  12795.7  12783.7  12790.2          288   

       spread  real_volume  trade_volume  
0         400            0           0.5  
1         400            0           0.5  
2         400            0           0.5  
3         400            0           0.5  
4         400            0           0.5  
...       ...          ...           ...  
34192     120            0           0.5  
34193     120            0           0.5  
34194     120            0           0.5  
34195     120            0           0.5  
34196     120            0           0.5  

[34197 rows x 9 columns]

In [83]:
bars['sma_100'] = bars['close'].rolling(100).mean()
bars['sma_10'] = bars['close'].rolling(10).mean()
bars['hour'] = bars['time'].dt.hour
bars

time     open     high      low    close  tick_volume  \
0     2022-01-03 02:15:00  15886.7  15889.2  15881.2  15884.0           32   
1     2022-01-03 02:20:00  15884.0  15900.0  15884.0  15900.0           42   
2     2022-01-03 02:25:00  15903.0  15938.0  15902.5  15938.0           74   
3     2022-01-03 02:30:00  15936.0  15936.0  15918.0  15918.0           36   
4     2022-01-03 02:35:00  15918.0  15925.5  15911.5  15911.5           29   
...                   ...      ...      ...      ...      ...          ...   
34192 2022-06-30 21:40:00  12817.2  12817.2  12788.2  12789.2          282   
34193 2022-06-30 21:45:00  12788.2  12801.2  12786.7  12795.7          263   
34194 2022-06-30 21:50:00  12795.2  12797.2  12778.7  12785.7          247   
34195 2022-06-30 21:55:00  12785.2  12789.2  12780.2  12786.2          232   
34196 2022-06-30 22:00:00  12785.7  12795.7  12783.7  12790.2          288   

       spread  real_volume  trade_volume    sma_100    sma_10  hour  
0         400            0           0.5        NaN       NaN     2  
1         400            0           0.5        NaN       NaN     2  
2         400            0           0.5        NaN       NaN     2  
3         400            0           0.5        NaN       NaN     2  
4         400            0           0.5        NaN       NaN     2  
...       ...          ...           ...        ...       ...   ...  
34192     120            0           0.5  12730.179  12817.85    21  
34193     120            0           0.5  12731.305  12814.65    21  
34194     120            0           0.5  12732.346  12809.90    21  
34195     120            0           0.5  12733.647  12806.65    21  
34196     120            0           0.5  12734.968  12803.85    22  

[34197 rows x 12 columns]

In [84]:
bars2 = bars.dropna().copy()

def get_signal(x):

    if 9 <= x['hour'] <= 18:

        if x['sma_10'] > x['sma_100']:
            return 1
        elif x['sma_10'] < x['sma_100']:
            return -1

    return 0

bars2['signal'] = bars2.apply(get_signal, axis=1)
bars2['prev_price'] = bars2['close'].shift(1)
bars2['price_change'] = bars2['close'] - bars2['prev_price']

bars2['signal_change'] = (bars2['signal'] - bars2['signal'].shift(1)).abs()
bars2['commission'] = bars2.apply(lambda x: commission * x['signal_change'] * x['trade_volume'], axis=1)
bars2

time     open     high      low    close  tick_volume  \
99    2022-01-03 10:30:00  16027.2  16029.7  16015.7  16018.2          289   
100   2022-01-03 10:35:00  16018.2  16034.7  16017.7  16029.7          282   
101   2022-01-03 10:40:00  16028.7  16056.7  16023.7  16047.7          264   
102   2022-01-03 10:45:00  16047.2  16049.2  16036.2  16037.7          245   
103   2022-01-03 10:50:00  16037.7  16043.7  16022.7  16027.7          302   
...                   ...      ...      ...      ...      ...          ...   
34192 2022-06-30 21:40:00  12817.2  12817.2  12788.2  12789.2          282   
34193 2022-06-30 21:45:00  12788.2  12801.2  12786.7  12795.7          263   
34194 2022-06-30 21:50:00  12795.2  12797.2  12778.7  12785.7          247   
34195 2022-06-30 21:55:00  12785.2  12789.2  12780.2  12786.2          232   
34196 2022-06-30 22:00:00  12785.7  12795.7  12783.7  12790.2          288   

       spread  real_volume  trade_volume    sma_100    sma_10  hour  signal  \
99         50            0           0.5  15897.243  15968.85    10       1   
100        50            0           0.5  15898.700  15983.00    10       1   
101        50            0           0.5  15900.177  15998.10    10       1   
102        50            0           0.5  15901.174  16009.35    10       1   
103        50            0           0.5  15902.271  16017.00    10       1   
...       ...          ...           ...        ...       ...   ...     ...   
34192     120            0           0.5  12730.179  12817.85    21       0   
34193     120            0           0.5  12731.305  12814.65    21       0   
34194     120            0           0.5  12732.346  12809.90    21       0   
34195     120            0           0.5  12733.647  12806.65    21       0   
34196     120            0           0.5  12734.968  12803.85    22       0   

       prev_price  price_change  signal_change  commission  
99            NaN           NaN            NaN         NaN  
100       16018.2          11.5            0.0         0.0  
101       16029.7          18.0            0.0         0.0  
102       16047.7         -10.0            0.0         0.0  
103       16037.7         -10.0            0.0         0.0  
...           ...           ...            ...         ...  
34192     12816.2         -27.0            0.0         0.0  
34193     12789.2           6.5            0.0         0.0  
34194     12795.7         -10.0            0.0         0.0  
34195     12785.7           0.5            0.0         0.0  
34196     12786.2           4.0            0.0         0.0  

[34098 rows x 17 columns]

In [85]:
bars3 = bars2.dropna().copy()
bars3['profit'] = bars3['signal'] * bars3['price_change'] * bars3['trade_volume']
bars3['gross_profit'] = bars3['profit'].cumsum()

bars3['net_profit'] = bars3['gross_profit'] - bars3['commission'].cumsum()


bars3

time     open     high      low    close  tick_volume  \
100   2022-01-03 10:35:00  16018.2  16034.7  16017.7  16029.7          282   
101   2022-01-03 10:40:00  16028.7  16056.7  16023.7  16047.7          264   
102   2022-01-03 10:45:00  16047.2  16049.2  16036.2  16037.7          245   
103   2022-01-03 10:50:00  16037.7  16043.7  16022.7  16027.7          302   
104   2022-01-03 10:55:00  16027.7  16029.7  16011.7  16015.7          200   
...                   ...      ...      ...      ...      ...          ...   
34192 2022-06-30 21:40:00  12817.2  12817.2  12788.2  12789.2          282   
34193 2022-06-30 21:45:00  12788.2  12801.2  12786.7  12795.7          263   
34194 2022-06-30 21:50:00  12795.2  12797.2  12778.7  12785.7          247   
34195 2022-06-30 21:55:00  12785.2  12789.2  12780.2  12786.2          232   
34196 2022-06-30 22:00:00  12785.7  12795.7  12783.7  12790.2          288   

       spread  real_volume  trade_volume    sma_100    sma_10  hour  signal  \
100        50            0           0.5  15898.700  15983.00    10       1   
101        50            0           0.5  15900.177  15998.10    10       1   
102        50            0           0.5  15901.174  16009.35    10       1   
103        50            0           0.5  15902.271  16017.00    10       1   
104        50            0           0.5  15903.313  16022.80    10       1   
...       ...          ...           ...        ...       ...   ...     ...   
34192     120            0           0.5  12730.179  12817.85    21       0   
34193     120            0           0.5  12731.305  12814.65    21       0   
34194     120            0           0.5  12732.346  12809.90    21       0   
34195     120            0           0.5  12733.647  12806.65    21       0   
34196     120            0           0.5  12734.968  12803.85    22       0   

       prev_price  price_change  signal_change  commission  profit  \
100       16018.2          11.5            0.0         0.0    5.75   
101       16029.7          18.0            0.0         0.0    9.00   
102       16047.7         -10.0            0.0         0.0   -5.00   
103       16037.7         -10.0            0.0         0.0   -5.00   
104       16027.7         -12.0            0.0         0.0   -6.00   
...           ...           ...            ...         ...     ...   
34192     12816.2         -27.0            0.0         0.0   -0.00   
34193     12789.2           6.5            0.0         0.0    0.00   
34194     12795.7         -10.0            0.0         0.0   -0.00   
34195     12785.7           0.5            0.0         0.0    0.00   
34196     12786.2           4.0            0.0         0.0    0.00   

       gross_profit  net_profit  
100            5.75        5.75  
101           14.75       14.75  
102            9.75        9.75  
103            4.75        4.75  
104           -1.25       -1.25  
...             ...         ...  
34192       2759.50     2362.00  
34193       2759.50     2362.00  
34194       2759.50     2362.00  
34195       2759.50     2362.00  
34196       2759.50     2362.00  

[34097 rows x 20 columns]

In [87]:
px.line(bars3, 'time', ['gross_profit', 'net_profit'], title="DE40 Backtest MA Trendfollowing")